In [1]:
import requests
from bs4 import BeautifulSoup
import pandas as pd
from datetime import datetime
import warnings
import time
import sklearn.preprocessing

pd.set_option("display.max_columns", None)
warnings.filterwarnings(action='ignore')

serviceKey='bwUUK6MEA6GnqDpo2ZS9ChN4VZ1nkUPXrryU80XxUcLqxB62pIGIPWXNdyzqgT20BHrw8zxWWk9rqiSQwTrbnQ=='

p7000 ={'serviceKey' :serviceKey,
             'routeId':'200000112','stationId':'228000703'}
class Bus():
    def __init__(self,params):
        self.params=params
        self.bus_time=[]
        
    def repet(self):
        url = 'http://apis.data.go.kr/6410000/busarrivalservice/getBusArrivalItem'
        response = requests.get(url, params=self.params)
        soup=BeautifulSoup(response.text,'xml')
        return soup

        
    def current_buses(self): 
        url = 'http://apis.data.go.kr/6410000/buslocationservice/getBusLocationList'
        mod_params ={'serviceKey' : self.params['serviceKey'],
                  'routeId':self.params['routeId']}

        response=requests.get(url,params=mod_params)
        soup=BeautifulSoup(response.text,'xml')
        locations=sorted([int(x.stationSeq.text) for x in soup.find_all('busLocationList')])
        return locations


def trim_data(df,FileName):
    df['시간'] = df['시간'].apply(pd.to_datetime)
    df['hour']=df['시간'].dt.hour
    df['minute']=df['시간'].dt.minute
    df['second']=df['시간'].dt.second
    df['day'] = df['시간'].dt.weekday 

    mb = sklearn.preprocessing.MultiLabelBinarizer()
    if isinstance(df['운행중인 다른 버스들의 위치'].iloc[0], str):
        df['운행중인 다른 버스들의 위치'] = df['운행중인 다른 버스들의 위치'].apply(eval)
    entity = mb.fit_transform(df['운행중인 다른 버스들의 위치']) 
    lsts=pd.DataFrame(entity,columns=mb.classes_)
    lsts.columns=[f'station{x}' for x in lsts.columns]
    df=pd.concat([df,lsts],axis=1,sort=False).reset_index(drop=True)


    df=df.drop(["운행중인 다른 버스들의 위치"],axis=1)
    
    batch=df.index[df.arrived==1]
    df=df.iloc[:batch[-1]+1,:]
    #7/12 -----------------------------------
    batch=df.index[df.arrived==1]
    temp=0
    for x in batch:
        for y in range(temp,x): 
            df['arrived'][y]=(df['시간'][x]-df['시간'][y]).seconds
            temp=x+1
    for e in batch:
        df['arrived'][e]=0
    # 7/12 -----------------------------------

    df = df.set_index('시간')
    df.to_csv(f'./{FileName}')        # 동일 폴더에 파일이 저장될 거임
    return df





In [ ]:
past=4
pBus=Bus(p7000)
for x in range(720): # 시간 설정
    soup=pBus.repet()
    try:
        result=int(soup.resultCode.text)
        arrived=0
        if past!=result:
            if result==0:
                arrived=1
        pBus.bus_time.append([soup.queryTime.text,pBus.current_buses(),arrived])
        past=result
        print(x,"번째 시도: ",pBus.bus_time)
        time.sleep(60)
    except Exception as e:
        continue

df=pd.DataFrame(pBus.bus_time,columns=['시간','운행중인 다른 버스들의 위치','arrived'])

mod_df=trim_data(df,'7000_thu.csv') # 이름 설정
mod_df

0 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0]]
1 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0]]
2 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0]]
3 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0]]
4 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64]

17 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 16

24 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 16

29 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 16

34 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 16

...

392 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 1

393 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 1

394 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 1

395 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 1

396 번째 시도:  [['2022-08-04 11:08:14.630', [7, 16, 26, 30, 39, 51, 62, 78], 0], ['2022-08-04 11:09:14.801', [8, 16, 26, 31, 40, 51, 63, 79], 0], ['2022-08-04 11:10:15.003', [8, 17, 26, 31, 40, 52, 63], 0], ['2022-08-04 11:11:15.143', [9, 18, 26, 32, 40, 52, 63], 0], ['2022-08-04 11:12:15.299', [9, 18, 27, 32, 41, 52, 64], 0], ['2022-08-04 11:13:15.423', [10, 19, 27, 33, 41, 52, 65], 0], ['2022-08-04 11:14:15.579', [10, 19, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:15:15.750', [11, 21, 28, 33, 42, 53, 65], 0], ['2022-08-04 11:16:16.781', [1, 11, 21, 29, 34, 44, 54, 67], 1], ['2022-08-04 11:17:17.453', [3, 11, 22, 29, 35, 45, 55, 68], 0], ['2022-08-04 11:18:18.624', [3, 13, 24, 29, 36, 45, 56, 68], 0], ['2022-08-04 11:19:18.842', [3, 13, 24, 31, 37, 45, 56, 69], 0], ['2022-08-04 11:20:18.998', [4, 13, 24, 31, 37, 46, 57, 69], 0], ['2022-08-04 11:21:19.169', [5, 14, 25, 31, 38, 47, 58, 70], 0], ['2022-08-04 11:22:19.356', [7, 16, 26, 32, 38, 47, 59, 71], 0], ['2022-08-04 11:23:19.543', [8, 1